In [1]:
from sklearn.metrics import roc_auc_score
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
import lightgbm as lgb

In [2]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')

In [3]:
target = train['target']
train = train.drop(['id', 'target'], axis = 1)

In [4]:
sub = pd.read_csv('sample_submission.csv')
sub['id'] = test['id']
test = test.drop('id', axis = 1)

In [5]:
for c in train.columns:
    col_type = train[c].dtype
    if col_type == 'object' or col_type.name == 'category':
        train[c] = train[c].astype('category')
        test[c] = test[c].astype('category')

In [ ]:
import optuna
from sklearn.model_selection import train_test_split
import warnings
warnings.filterwarnings("ignore")

def objective(trial, data=train, target=target):

    train_x, test_x, train_y, test_y = train_test_split(data, target, test_size=0.25, stratify = target, shuffle = True, random_state=2021)
    param = {
        'n_estimators': 200000,
        'num_leaves': trial.suggest_int('num_leaves', 2, 500),
        'max_depth': trial.suggest_categorical('max_depth', [-1,20, 30,50,80, 100,200, 300]),
        'reg_alpha': trial.suggest_float('reg_alpha', 1E-5, 100),
        'reg_lambda': trial.suggest_float('reg_lambda', 1E-5, 100),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 1E-3, 1.0),
        #'subsample': trial.suggest_float('subsample ', 1E-16, 1.0),
        'cat_smooth': trial.suggest_float('cat_smooth', 1.0, 100),  
        'subsample': trial.suggest_categorical('subsample', [0.2,0.3,0.4,0.5,0.6,0.7,0.8,1.0]),
        'min_child_samples': trial.suggest_int('min_child_samples', 1, 300),
        'min_child_weight': trial.suggest_loguniform('min_child_weight', 1E-3, 10),
        'subsample_freq': trial.suggest_int('subsample_freq', 0, 20),
        'metric': 'auc', 
        'random_state': 2021,
        'learning_rate': trial.suggest_loguniform('learning_rate', 1E-3, 1.0) 
        
    }

    model = lgb.LGBMClassifier(**param)  
    model.fit(train_x,train_y,eval_set=[(test_x,test_y)],early_stopping_rounds=50,verbose=False)

    preds = model.predict_proba(test_x)[:, 1]    
    roc = roc_auc_score(test_y, preds)
    
    return roc

study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100)
print('Best trial:', study.best_params)

[I 2021-03-06 13:57:27,712] A new study created in memory with name: no-name-da19a6d9-992e-4a0f-95d2-c5be186c12c1
[I 2021-03-06 13:59:17,452] Trial 0 finished with value: 0.8931723841653478 and parameters: {'num_leaves': 247, 'max_depth': 200, 'reg_alpha': 99.11316751866872, 'reg_lambda': 52.93689133708069, 'colsample_bytree': 0.8479006643738163, 'cat_smooth': 67.12114794730324, 'subsample': 0.5, 'min_child_samples': 124, 'min_child_weight': 0.004180115840202385, 'subsample_freq': 11, 'learning_rate': 0.013938402739817338}. Best is trial 0 with value: 0.8931723841653478.
[I 2021-03-06 13:59:40,781] Trial 1 finished with value: 0.890585726803653 and parameters: {'num_leaves': 366, 'max_depth': 100, 'reg_alpha': 88.35194042206997, 'reg_lambda': 1.724083631528075, 'colsample_bytree': 0.4049433363376084, 'cat_smooth': 9.499478025181114, 'subsample': 0.2, 'min_child_samples': 61, 'min_child_weight': 5.362928802048794, 'subsample_freq': 5, 'learning_rate': 0.04512460928654692}. Best is trial

[I 2021-03-06 14:45:56,931] Trial 17 finished with value: 0.8786106545654557 and parameters: {'num_leaves': 422, 'max_depth': 100, 'reg_alpha': 73.33024900392974, 'reg_lambda': 26.88157955719796, 'colsample_bytree': 0.7161915380911396, 'cat_smooth': 60.326412270393725, 'subsample': 0.5, 'min_child_samples': 192, 'min_child_weight': 0.001023500360482126, 'subsample_freq': 0, 'learning_rate': 0.0021754817966796324}. Best is trial 15 with value: 0.8966903893381533.
[I 2021-03-06 14:46:32,787] Trial 18 finished with value: 0.8921946234936551 and parameters: {'num_leaves': 279, 'max_depth': 20, 'reg_alpha': 2.0066821463981412, 'reg_lambda': 39.563016093969956, 'colsample_bytree': 0.9769595134465352, 'cat_smooth': 1.1857118831470803, 'subsample': 0.7, 'min_child_samples': 236, 'min_child_weight': 0.0011501557407765798, 'subsample_freq': 9, 'learning_rate': 0.07789506794389234}. Best is trial 15 with value: 0.8966903893381533.
[I 2021-03-06 14:54:41,445] Trial 19 finished with value: 0.895932

[I 2021-03-06 15:39:43,132] Trial 35 finished with value: 0.8978423913424319 and parameters: {'num_leaves': 495, 'max_depth': 300, 'reg_alpha': 4.249841267075523, 'reg_lambda': 54.90206472933877, 'colsample_bytree': 0.44426801909405683, 'cat_smooth': 80.68820321367292, 'subsample': 0.8, 'min_child_samples': 132, 'min_child_weight': 0.01238134849505037, 'subsample_freq': 11, 'learning_rate': 0.011528771880600015}. Best is trial 32 with value: 0.8981347574864351.
[I 2021-03-06 15:46:46,345] Trial 36 finished with value: 0.8974655883776659 and parameters: {'num_leaves': 445, 'max_depth': 80, 'reg_alpha': 11.422795230650104, 'reg_lambda': 68.49718630925652, 'colsample_bytree': 0.5320658810524015, 'cat_smooth': 91.28548070516096, 'subsample': 0.8, 'min_child_samples': 101, 'min_child_weight': 0.02749996896593859, 'subsample_freq': 6, 'learning_rate': 0.00836602888428692}. Best is trial 32 with value: 0.8981347574864351.
[I 2021-03-06 16:06:31,354] Trial 37 finished with value: 0.89829211054

[I 2021-03-06 19:21:17,303] Trial 53 finished with value: 0.8971663151775527 and parameters: {'num_leaves': 482, 'max_depth': 300, 'reg_alpha': 3.217601207914842, 'reg_lambda': 58.172836450958876, 'colsample_bytree': 0.32994896932178824, 'cat_smooth': 57.39948432810212, 'subsample': 0.2, 'min_child_samples': 147, 'min_child_weight': 0.01255135700740579, 'subsample_freq': 6, 'learning_rate': 0.006662373341109387}. Best is trial 37 with value: 0.8982921105418405.
[I 2021-03-06 19:38:47,647] Trial 54 finished with value: 0.8977095348257489 and parameters: {'num_leaves': 435, 'max_depth': 300, 'reg_alpha': 8.788030449895222, 'reg_lambda': 65.77008030525444, 'colsample_bytree': 0.279618087672768, 'cat_smooth': 70.21420409386306, 'subsample': 0.8, 'min_child_samples': 122, 'min_child_weight': 0.006515632803105264, 'subsample_freq': 10, 'learning_rate': 0.004221082447744282}. Best is trial 37 with value: 0.8982921105418405.
[I 2021-03-06 19:43:25,932] Trial 55 finished with value: 0.897379767

[I 2021-03-06 22:38:22,545] Trial 71 finished with value: 0.898136099637457 and parameters: {'num_leaves': 336, 'max_depth': 20, 'reg_alpha': 10.227422821533972, 'reg_lambda': 51.710805819574475, 'colsample_bytree': 0.23875803260180614, 'cat_smooth': 56.77647468401155, 'subsample': 0.8, 'min_child_samples': 49, 'min_child_weight': 0.0027328024030756444, 'subsample_freq': 8, 'learning_rate': 0.007165362359227403}. Best is trial 62 with value: 0.8984307949156489.


In [11]:
num_folds = 10
train_oof_lgb2 = np.zeros(train.shape[0])   
test_preds_2 = 0
auc_2 = []

kf = StratifiedKFold(n_splits =num_folds, shuffle = True, random_state = 2021 )

for f, (train_idx, val_idx) in  enumerate(kf.split(train, target)) :
    train_df, val_df = train.iloc[train_idx], train.iloc[val_idx]
    train_t, val_t = target.iloc[train_idx], target.iloc[val_idx]
    
    param= {'n_estimators' : 200000, 'num_leaves': 184, 'max_depth': 200, 'reg_alpha': 0.10676733310102549, 'reg_lambda': 96.02065004762423, 
            'colsample_bytree': 0.22195509228191793, 'cat_smooth': 12.131095735803058, 'subsample': 0.8, 'min_child_samples': 180, 
            'min_child_weight': 0.383685024678385, 'subsample_freq': 15, 'learning_rate': 0.0017638047414559395, 'metric' : 'auc', 'random_state' : 2021}
    
    model = lgb.LGBMClassifier(**param)
    model.fit(train_df, train_t, early_stopping_rounds = 50, verbose = True, eval_set = [(train_df, train_t),(val_df, val_t)])    
    temp_oof = model.predict_proba(val_df)[:, 1]
    temp_test = model.predict_proba(test)[:, 1]
    train_oof_lgb2[val_idx] = temp_oof
    test_preds_2 += temp_test / num_folds
    auc_2.append(roc_auc_score(val_t, model.predict_proba(val_df)[:, 1])) 

C:\Users\pooja\anaconda3\lib\site-packages\lightgbm\basic.py:1286: UserWarning: Overriding the parameters from Reference Dataset.
  warnings.warn('Overriding the parameters from Reference Dataset.')
C:\Users\pooja\anaconda3\lib\site-packages\lightgbm\basic.py:1098: UserWarning: categorical_column in param dict is overridden.
  warnings.warn('{} in param dict is overridden.'.format(cat_alias))


[1]	training's auc: 0.747592	valid_1's auc: 0.744218
Training until validation scores don't improve for 50 rounds
[2]	training's auc: 0.846502	valid_1's auc: 0.845224
[3]	training's auc: 0.847728	valid_1's auc: 0.845666
[4]	training's auc: 0.863345	valid_1's auc: 0.862214
[5]	training's auc: 0.871081	valid_1's auc: 0.869487
[6]	training's auc: 0.872811	valid_1's auc: 0.871142
[7]	training's auc: 0.875085	valid_1's auc: 0.873747
[8]	training's auc: 0.876641	valid_1's auc: 0.875214
[9]	training's auc: 0.876948	valid_1's auc: 0.87529
[10]	training's auc: 0.876916	valid_1's auc: 0.875225
[11]	training's auc: 0.877818	valid_1's auc: 0.87585
[12]	training's auc: 0.878665	valid_1's auc: 0.876904
[13]	training's auc: 0.87901	valid_1's auc: 0.877277
[14]	training's auc: 0.87956	valid_1's auc: 0.877428
[15]	training's auc: 0.880202	valid_1's auc: 0.878026
[16]	training's auc: 0.880827	valid_1's auc: 0.878772
[17]	training's auc: 0.880804	valid_1's auc: 0.878462
[18]	training's auc: 0.881082	vali

[152]	training's auc: 0.884649	valid_1's auc: 0.882908
[153]	training's auc: 0.884751	valid_1's auc: 0.883016
[154]	training's auc: 0.884783	valid_1's auc: 0.883048
[155]	training's auc: 0.884719	valid_1's auc: 0.88298
[156]	training's auc: 0.884749	valid_1's auc: 0.883005
[157]	training's auc: 0.884771	valid_1's auc: 0.883021
[158]	training's auc: 0.884815	valid_1's auc: 0.883078
[159]	training's auc: 0.884763	valid_1's auc: 0.883032
[160]	training's auc: 0.884751	valid_1's auc: 0.883024
[161]	training's auc: 0.884734	valid_1's auc: 0.882992
[162]	training's auc: 0.884712	valid_1's auc: 0.882969
[163]	training's auc: 0.884694	valid_1's auc: 0.882947
[164]	training's auc: 0.88469	valid_1's auc: 0.882961
[165]	training's auc: 0.884686	valid_1's auc: 0.882962
[166]	training's auc: 0.884667	valid_1's auc: 0.88294
[167]	training's auc: 0.884637	valid_1's auc: 0.882888
[168]	training's auc: 0.88463	valid_1's auc: 0.882903
[169]	training's auc: 0.884625	valid_1's auc: 0.882889
[170]	training

[303]	training's auc: 0.885364	valid_1's auc: 0.883776
[304]	training's auc: 0.885408	valid_1's auc: 0.883821
[305]	training's auc: 0.885419	valid_1's auc: 0.883829
[306]	training's auc: 0.885408	valid_1's auc: 0.883821
[307]	training's auc: 0.885383	valid_1's auc: 0.883795
[308]	training's auc: 0.885397	valid_1's auc: 0.883797
[309]	training's auc: 0.885402	valid_1's auc: 0.88381
[310]	training's auc: 0.885408	valid_1's auc: 0.883803
[311]	training's auc: 0.88539	valid_1's auc: 0.883782
[312]	training's auc: 0.885398	valid_1's auc: 0.883798
[313]	training's auc: 0.885409	valid_1's auc: 0.883815
[314]	training's auc: 0.885407	valid_1's auc: 0.883818
[315]	training's auc: 0.88543	valid_1's auc: 0.883837
[316]	training's auc: 0.885451	valid_1's auc: 0.883851
[317]	training's auc: 0.885454	valid_1's auc: 0.883848
[318]	training's auc: 0.885481	valid_1's auc: 0.883874
[319]	training's auc: 0.885484	valid_1's auc: 0.883867
[320]	training's auc: 0.885494	valid_1's auc: 0.883873
[321]	trainin

[453]	training's auc: 0.886421	valid_1's auc: 0.884674
[454]	training's auc: 0.886426	valid_1's auc: 0.884685
[455]	training's auc: 0.886427	valid_1's auc: 0.884683
[456]	training's auc: 0.886426	valid_1's auc: 0.884682
[457]	training's auc: 0.886427	valid_1's auc: 0.884679
[458]	training's auc: 0.886441	valid_1's auc: 0.884686
[459]	training's auc: 0.886451	valid_1's auc: 0.884688
[460]	training's auc: 0.886444	valid_1's auc: 0.884685
[461]	training's auc: 0.88645	valid_1's auc: 0.88469
[462]	training's auc: 0.886448	valid_1's auc: 0.884688
[463]	training's auc: 0.886443	valid_1's auc: 0.884676
[464]	training's auc: 0.886446	valid_1's auc: 0.88467
[465]	training's auc: 0.88645	valid_1's auc: 0.884675
[466]	training's auc: 0.886464	valid_1's auc: 0.884687
[467]	training's auc: 0.886474	valid_1's auc: 0.884691
[468]	training's auc: 0.886478	valid_1's auc: 0.884702
[469]	training's auc: 0.88649	valid_1's auc: 0.884722
[470]	training's auc: 0.886496	valid_1's auc: 0.884724
[471]	training'

...

[11252]	training's auc: 0.920211	valid_1's auc: 0.89595
[11253]	training's auc: 0.920212	valid_1's auc: 0.89595
[11254]	training's auc: 0.920215	valid_1's auc: 0.895951
[11255]	training's auc: 0.920217	valid_1's auc: 0.895951
[11256]	training's auc: 0.920219	valid_1's auc: 0.895951
[11257]	training's auc: 0.920221	valid_1's auc: 0.895951
[11258]	training's auc: 0.920223	valid_1's auc: 0.895952
[11259]	training's auc: 0.920225	valid_1's auc: 0.895952
[11260]	training's auc: 0.920226	valid_1's auc: 0.895952
[11261]	training's auc: 0.920228	valid_1's auc: 0.895952
[11262]	training's auc: 0.92023	valid_1's auc: 0.895953
[11263]	training's auc: 0.920232	valid_1's auc: 0.895953
[11264]	training's auc: 0.920234	valid_1's auc: 0.895953
[11265]	training's auc: 0.920236	valid_1's auc: 0.895952
[11266]	training's auc: 0.920238	valid_1's auc: 0.895952
[11267]	training's auc: 0.92024	valid_1's auc: 0.895952
[11268]	training's auc: 0.920242	valid_1's auc: 0.895952
[11269]	training's auc: 0.920243	va

[11397]	training's auc: 0.920488	valid_1's auc: 0.895976
[11398]	training's auc: 0.92049	valid_1's auc: 0.895977
[11399]	training's auc: 0.920492	valid_1's auc: 0.895976
[11400]	training's auc: 0.920495	valid_1's auc: 0.895977
[11401]	training's auc: 0.920496	valid_1's auc: 0.895976
[11402]	training's auc: 0.920498	valid_1's auc: 0.895977
[11403]	training's auc: 0.9205	valid_1's auc: 0.895977
[11404]	training's auc: 0.920502	valid_1's auc: 0.895978
[11405]	training's auc: 0.920504	valid_1's auc: 0.895977
[11406]	training's auc: 0.920506	valid_1's auc: 0.895977
[11407]	training's auc: 0.920508	valid_1's auc: 0.895977
[11408]	training's auc: 0.920509	valid_1's auc: 0.895978
[11409]	training's auc: 0.920512	valid_1's auc: 0.895977
[11410]	training's auc: 0.920514	valid_1's auc: 0.895978
[11411]	training's auc: 0.920515	valid_1's auc: 0.895978
[11412]	training's auc: 0.920517	valid_1's auc: 0.895977
[11413]	training's auc: 0.920518	valid_1's auc: 0.895977
[11414]	training's auc: 0.920521	v

[11545]	training's auc: 0.920763	valid_1's auc: 0.896
[11546]	training's auc: 0.920765	valid_1's auc: 0.896
[11547]	training's auc: 0.920767	valid_1's auc: 0.896
[11548]	training's auc: 0.920768	valid_1's auc: 0.896
[11549]	training's auc: 0.92077	valid_1's auc: 0.896
[11550]	training's auc: 0.920772	valid_1's auc: 0.896
[11551]	training's auc: 0.920774	valid_1's auc: 0.896001
[11552]	training's auc: 0.920776	valid_1's auc: 0.896002
[11553]	training's auc: 0.920778	valid_1's auc: 0.896002
[11554]	training's auc: 0.920779	valid_1's auc: 0.896003
[11555]	training's auc: 0.920781	valid_1's auc: 0.896003
[11556]	training's auc: 0.920783	valid_1's auc: 0.896002
[11557]	training's auc: 0.920784	valid_1's auc: 0.896002
[11558]	training's auc: 0.920786	valid_1's auc: 0.896002
[11559]	training's auc: 0.920788	valid_1's auc: 0.896002
[11560]	training's auc: 0.92079	valid_1's auc: 0.896002
[11561]	training's auc: 0.920792	valid_1's auc: 0.896002
[11562]	training's auc: 0.920794	valid_1's auc: 0.8

[11690]	training's auc: 0.921034	valid_1's auc: 0.896018
[11691]	training's auc: 0.921036	valid_1's auc: 0.896018
[11692]	training's auc: 0.921038	valid_1's auc: 0.896019
[11693]	training's auc: 0.92104	valid_1's auc: 0.896019
[11694]	training's auc: 0.921041	valid_1's auc: 0.896018
[11695]	training's auc: 0.921044	valid_1's auc: 0.896019
[11696]	training's auc: 0.921045	valid_1's auc: 0.896019
[11697]	training's auc: 0.921047	valid_1's auc: 0.896019
[11698]	training's auc: 0.92105	valid_1's auc: 0.896019
[11699]	training's auc: 0.921052	valid_1's auc: 0.896019
[11700]	training's auc: 0.921054	valid_1's auc: 0.89602
[11701]	training's auc: 0.921055	valid_1's auc: 0.89602
[11702]	training's auc: 0.921058	valid_1's auc: 0.89602
[11703]	training's auc: 0.92106	valid_1's auc: 0.89602
[11704]	training's auc: 0.921062	valid_1's auc: 0.89602
[11705]	training's auc: 0.921063	valid_1's auc: 0.89602
[11706]	training's auc: 0.921065	valid_1's auc: 0.89602
[11707]	training's auc: 0.921067	valid_1'

[11978]	training's auc: 0.921576	valid_1's auc: 0.896056
[11979]	training's auc: 0.921577	valid_1's auc: 0.896057
[11980]	training's auc: 0.921579	valid_1's auc: 0.896057
[11981]	training's auc: 0.921581	valid_1's auc: 0.896058
[11982]	training's auc: 0.921582	valid_1's auc: 0.896058
[11983]	training's auc: 0.921585	valid_1's auc: 0.896058
[11984]	training's auc: 0.921587	valid_1's auc: 0.896058
[11985]	training's auc: 0.921587	valid_1's auc: 0.896058
[11986]	training's auc: 0.921589	valid_1's auc: 0.896058
[11987]	training's auc: 0.921592	valid_1's auc: 0.896058
[11988]	training's auc: 0.921593	valid_1's auc: 0.896058
[11989]	training's auc: 0.921595	valid_1's auc: 0.896058
[11990]	training's auc: 0.921595	valid_1's auc: 0.896058
[11991]	training's auc: 0.921597	valid_1's auc: 0.896059
[11992]	training's auc: 0.921599	valid_1's auc: 0.896059
[11993]	training's auc: 0.921601	valid_1's auc: 0.89606
[11994]	training's auc: 0.921604	valid_1's auc: 0.89606
[11995]	training's auc: 0.921606	

In [12]:
np.mean(auc_2)

0.8972212105714357

In [13]:
roc_auc_score(target, train_oof_lgb2)

0.8972071302592074